# R

using the [RCall.jl](https://juliainterop.github.io/RCall.jl/stable/) package.

In [1]:
using Printf, DelimitedFiles, LinearAlgebra, Statistics

include("jlFiles/printmat.jl")
include("jlFiles/OlsNW.jl")         #functions for OLS

CovNWFn

In [2]:
x = readdlm("Data/FFmFactorsPs.csv",',',skipstart=1)

                #yearmonth, market, small minus big, high minus low
(ym,Rme,RSMB,RHML) = (x[:,1],x[:,2]/100,x[:,3]/100,x[:,4]/100) 
x = nothing

printlnPs("Sample size:",size(Rme))

Sample size:    (388,)


# Do OLS (in Julia)

use the function sin the file OlsNW.jl to do OLS. Report point estimates and standard errors.

In [3]:
Y = Rme
T = size(Y,1)
X = [ones(T) RSMB RHML]

(b,u,Yhat,V,R2) = OlsGMFn(Y,X)
std_iid = sqrt.(diag(V))

printblue("OLS Results (assuming iid residuals):\n")
xNames = ["c","SMB","HML"]
printmat([b std_iid],colNames=["b","std_iid"],rowNames=xNames)

OLS Results (assuming iid residuals):

            b   std_iid
c       0.007     0.002
SMB     0.217     0.073
HML    -0.429     0.074



# Getting Started with RCall

In [4]:
using RCall

In [5]:
@rput X Y

ResultsR = reval("summary(mod <- lm(Y ~ X+0))")       #print summary of regression
println(ResultsR)

resultsR = reval("mod <- lm(Y ~ X+0)")                #get all output

RObject{VecSxp}

Call:
lm(formula = Y ~ X + 0)

Residuals:
     Min       1Q   Median       3Q      Max 
-0.20224 -0.02477  0.00335  0.02663  0.11840 

Coefficients:
    Estimate Std. Error t value Pr(>|t|)    
X1  0.006983   0.002205   3.167  0.00166 ** 
X2  0.216968   0.073565   2.949  0.00338 ** 
X3 -0.429088   0.073710  -5.821 1.23e-08 ***
---
Signif. codes:  0 '***' 0.001 '**' 0.01 '*' 0.05 '.' 0.1 ' ' 1

Residual standard error: 0.04295 on 385 degrees of freedom
Multiple R-squared:  0.1488,	Adjusted R-squared:  0.1422 
F-statistic: 22.44 on 3 and 385 DF,  p-value: 2.07e-13




RObject{VecSxp}

Call:
lm(formula = Y ~ X + 0)

Coefficients:
       X1         X2         X3  
 0.006983   0.216968  -0.429088  



In [6]:
println(names(resultsR))           #print all keys (field names)

[:coefficients, :residuals, :effects, :rank, Symbol("fitted.values"), :assign, :qr, Symbol("df.residual"), :xlevels, :call, :terms, :model]


# Task 1

Print the Julia and Python estimates (of the coefficients) in a table so we can compare directly.

# Task 2

Print the smallest and largest values of the difference between the residuals according to Julia and those according to Python.

# OLS (in Julia) with Robust Standard Errors

Use standard errors that are robust to heteroskedastcity and autocorrelation (2 lags).

In [9]:
(b,u,Yhat,V,R2) = OlsNWFn(Y,X,2)
std_nw = sqrt.(diag(V))

printblue("OLS Results (robust std):\n")
xNames = ["c","SMB","HML"]
printmat([b std_nw],colNames=["b","std_nw"],rowNames=xNames)

OLS Results (robust std):

            b    std_nw
c       0.007     0.002
SMB     0.217     0.129
HML    -0.429     0.118



# Task 3 

Now redo the R estimation with the same sort of robust standard errors. Hint: the `NeweyWest` in the `sandwich`package.